## Discrete Curvature and Spectral Meshes & Laplacian Mesh Smoothing

In [1]:
import igl
import scipy as sp
import numpy as np
from meshplot import plot
import matplotlib.pyplot as plt
import sys,os
import open3d as o3d 
import trimesh
import pyrender
import sklearn
from sklearn.neighbors import KDTree
from scipy.sparse import coo_matrix
from scipy.sparse.linalg import eigs

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


e:\Apps\uni\envs\geo_tutorials\lib\site-packages\pyglet\libs\win32\__init__.py:326: UserWarning: Could not set COM MTA mode. Unexpected behavior may occur.
  warnings.warn("Could not set COM MTA mode. Unexpected behavior may occur.")


#### Importing the meshes

In [2]:
RES_PATH = './meshes/'
CURVATURES_PATH = './meshes/curvatures/'
SMOOTHING_PATH = './meshes/smoothing/'
mesh_bunny = os.path.join(RES_PATH,'bunny.obj')
mesh_bcube = os.path.join(RES_PATH,'bumpy-cube-small.obj')
mesh_cube = os.path.join(RES_PATH,'cube.obj')
mesh_camel = os.path.join(RES_PATH,'camel.obj')
mesh_lilium = os.path.join(CURVATURES_PATH,'lilium_s.obj')
mesh_plane = os.path.join(CURVATURES_PATH,'plane.obj')
mesh_planens = os.path.join(SMOOTHING_PATH,'plane_ns.obj')
mesh_fandiskns = os.path.join(SMOOTHING_PATH,'fandisk_ns.obj')
assert os.path.exists(mesh_bunny), 'cannot found:'+mesh_bunny
assert os.path.exists(mesh_bcube), 'cannot found:'+mesh_bcube
assert os.path.exists(mesh_camel), 'cannot found:'+mesh_camel
assert os.path.exists(mesh_lilium), 'cannot found:'+mesh_lilium
assert os.path.exists(mesh_plane), 'cannot found:'+mesh_plane

In [3]:
bunny = trimesh.load_mesh(mesh_bunny)
bcube = trimesh.load_mesh(mesh_bcube)
cube = trimesh.load_mesh(mesh_cube)
camel = trimesh.load_mesh(mesh_camel)
lilium = trimesh.load_mesh(mesh_lilium)
plane = trimesh.load_mesh(mesh_plane)
armadillo = trimesh.load_mesh('armadillo.obj')
planens = trimesh.load_mesh(mesh_planens)
fandiskns = trimesh.load_mesh(mesh_fandiskns)

scene = trimesh.Scene(bcube)
scene.show()

#### Method that computes the Uniform Laplacian matrix

In [12]:
def UniformLaplacian(mesh):
    V = mesh.vertices
    F = mesh.faces
    n = V.shape[0]
    L = np.zeros((n, n))

    # Iterate over all vertices
    for i in range(V.shape[0]):
        # Set diagonal to -1
        L[i, i] = -1
        # Get neighbors
        neighbors = mesh.vertex_neighbors[i]
        # Set neighbors to 1 / number of neighbors
        L[i, neighbors] = 1 / len(neighbors)
        
    return L

#### Method that displays the Mean Curvature given a mesh and a laplacian

In [5]:
def showCurvature(laplace_fnc, mesh):
    # Compute the Laplacian
    L = laplace_fnc(mesh)
    # Applying the Laplacian to the manifold
    LXs = L @ mesh.vertices

    # Compute the mean curvature
    H = np.linalg.norm(LXs, axis=1) / 2
    # Normalize the mean curvature
    H_normalized = (H - H.min()) / (H.max() - H.min())

    # Colour the mesh according to the mean curvature
    print_mesh = mesh.copy()
    print_mesh.visual.vertex_colors = trimesh.visual.interpolate(H_normalized, color_map='jet')

    # Show the mesh
    scene = trimesh.Scene(print_mesh)
    return scene

#### Showing the results for different meshes

In [7]:
scene = showCurvature(UniformLaplacian, bunny)
scene.show()

In [11]:
scene = showCurvature(UniformLaplacian, bcube)
scene.show()

In [9]:
scene = showCurvature(UniformLaplacian, plane)
scene.show()

#### Method that computes the area given 3 vertices

In [15]:
def area(v1, v2, v3):
    edge1 = np.linalg.norm(v2 - v1)
    edge2 = np.linalg.norm(v3 - v1)
    edge3 = np.linalg.norm(v3 - v2)
    s = (edge1 + edge2 + edge3) / 2
    return np.sqrt(s * (s - edge1) * (s - edge2) * (s - edge3))

#### Method that determines the Gaussian Curvature matrix for a given mesh

In [13]:

def GaussianCurvature(mesh):
    V = mesh.vertices
    F = mesh.faces
    n = V.shape[0]
    K = np.zeros(n)
    
    # Iterate over all vertices
    for i in range(V.shape[0]):
        sumTheta = 0
        A_i = 0

        # Get faces
        faces = mesh.vertex_faces[i]
        faces = faces[faces != -1]
        
        # Iterate over all faces
        for face in faces:
            # Get points
            points = F[face]
            p1, p2 = points[points != i]

            # Compute theta angle
            v1 = V[i] - V[p1]
            v2 = V[i] - V[p2]

            sumTheta += np.arccos(np.dot(v1, v2) / (np.linalg.norm(v1) * np.linalg.norm(v2)))
            A_i += area(V[i], V[p1], V[p2])

        
        # Compute Gaussian curvature
        A_i /= 3
        K[i] = (2 * np.pi - sumTheta) / A_i
        
    return K


In [16]:
K = GaussianCurvature(bcube)

# Normalize the Gaussian curvature
K_normalized = (K - K.min()) / (K.max() - K.min())

print_bcube = bcube.copy()

# Colour the mesh according to the Gaussian curvature
print_bcube.visual.vertex_colors = trimesh.visual.interpolate(K_normalized)

scene = trimesh.Scene(print_bcube)
scene.show()

#### Method that determines the Discrete Laplace-Beltrami matrix

In [9]:
def DiscreteLaplaceBeltrami(mesh):
    V = mesh.vertices
    F = mesh.faces
    n = V.shape[0]

    # Define the sparse matrix for C and M^-1
    C_data = []
    C_row = []
    C_col = []
    M_inv_data = []
    M_inv_row = []
    M_inv_col = []

    # Iterate over all vertices
    for i in range(n):
        A_i = 0
        # Get faces
        faces = mesh.vertex_faces[i]
        faces = faces[faces != -1]

        # Find the start face
        # Determine the start face in the scenario where the faces do not cover all around the vertex
        d = {}
        for face in faces:
            points = F[face]
            for p in points:
                if p not in d:
                    d[p] = 1
                else:
                    d[p] += 1
        
        flag = True

        # Find the start face for this scenario as being a face that only has one neighbouring face
        for key in d:
            if d[key] == 1:
                start_face = [f for f in faces if key in F[f]][0]
                flag = False
                break

        # If we are not in this scenario, then we can just take the first face
        if flag:
            start_face = faces[0]
        
        # Starting with the find face, create a list of the faces in order
        # Meaning that they have a common edge
        my_faces = [start_face]
        cface = start_face

        # Set that has the faces that we have not yet added to the list
        set_faces = faces.tolist()
        set_faces.remove(cface)

        # While we have not added all faces to the list
        while len(set_faces) > 0:
            # Iterate over all faces
            for j in range(len(set_faces)):
                # Get the face's vertices
                f = F[set_faces[j]]
                # Find the common vertices with the current face
                common_points = [p for p in f if p in F[cface]]
                # If there are two common vertices, then we have found the next face
                if len(common_points) == 2:
                    cface = set_faces[j]
                    set_faces.remove(cface)
                    my_faces.append(cface)
                    break

        cotan_sum = 0
        for j in range(len(my_faces)):
            # Get the current and next face
            face = my_faces[j]
            face_after = my_faces[(j + 1) % len(my_faces)]

            # Get the points
            points = F[face]
            points_after = F[face_after]

            ps = points[points != i]
            ps_after = points_after[points_after != i]

            err = False

            # Determine which points are in common
            # p1 is the previous vertex, p2 is the j vertex that creates a common edge with the current vertex
            # p3 is the next vertex
            if ps[1] == ps_after[0]:
                p1 = ps[0]
                p2 = ps[1]
                p3 = ps_after[1]
            elif ps[1] == ps_after[1]:
                p1 = ps[0]
                p2 = ps[1]
                p3 = ps_after[0]
            elif ps[0] == ps_after[0]:
                p1 = ps[1]
                p2 = ps[0]
                p3 = ps_after[1]
            elif ps[0] == ps_after[1]:
                p1 = ps[1]
                p2 = ps[0]
                p3 = ps_after[0]
            else:
                err = True

            # Check for potential errors
            if not err:
                # Compute the edges
                v11 = V[p1] - V[i]
                v12 = V[p1] - V[p2]
                v21 = V[p3] - V[i]
                v22 = V[p3] - V[p2]
                
                # Compute the alpha and beta angles
                alpha = np.arccos(np.dot(v11, v12) / (np.linalg.norm(v11) * np.linalg.norm(v12)))
                beta = np.arccos(np.dot(v21, v22) / (np.linalg.norm(v21) * np.linalg.norm(v22)))

                # Compute the cotan sum
                cotan_sum += (np.cos(alpha) / np.sin(alpha)) + (np.cos(beta) / np.sin(beta))

                # Add the data to the sparse matrix
                C_data.append((np.cos(alpha) / np.sin(alpha)) + (np.cos(beta) / np.sin(beta)))
                C_row.append(i)
                C_col.append(p2)
            
            # Compute the area
            A_i += area(V[i], V[p1], V[p2])

        # Add the data to the sparse matrix
        C_data.append(-cotan_sum)
        C_row.append(i)
        C_col.append(i)
        M_inv_data.append(1 / (2 * A_i))
        M_inv_row.append(i)
        M_inv_col.append(i)

    # Create the sparse matrices
    C = coo_matrix((C_data, (C_row, C_col)), shape=(n, n))
    M_inv = coo_matrix((M_inv_data, (M_inv_row, M_inv_col)), shape=(n, n)).tocsr()

    # Compute the discrete Laplace-Beltrami operator
    L = M_inv @ C

    return L


#### Show the results for different meshes

In [47]:
scene = showCurvature(DiscreteLaplaceBeltrami, bcube)
scene.show()

In [48]:
scene = showCurvature(DiscreteLaplaceBeltrami, bunny)
scene.show()

In [49]:
scene = showCurvature(DiscreteLaplaceBeltrami, lilium)
scene.show()

In [50]:
scene = showCurvature(DiscreteLaplaceBeltrami, plane)
scene.show()

#### The following method determins the Spectral Analysis given a mesh, a Laplacian and the k number of eigenvectors

In [10]:
def spectralAnalysis(mesh, L, k):
    # Compute the eigenvectors and eigenvalues of the Laplace-Beltrami operator
    _, v = eigs(L, k=k, which='SM')

    x = np.zeros(mesh.vertices.shape[0])
    y = np.zeros(mesh.vertices.shape[0])
    z = np.zeros(mesh.vertices.shape[0])

    # Compute the coordinates of the vertices in the new basis
    for i in range(k):
        vi = np.real(v[:, i])
        x += np.dot(mesh.vertices[:, 0], vi) * vi
        y += np.dot(mesh.vertices[:, 1], vi) * vi
        z += np.dot(mesh.vertices[:, 2], vi) * vi

    # Reconstruct the mesh
    reconstructed_mesh = type(mesh)()
    reconstructed_mesh.vertices = np.column_stack((x, y, z))
    reconstructed_mesh.faces = mesh.faces

    return reconstructed_mesh


#### Running the algorithm on different k values and store the results

In [120]:
DLB = DiscreteLaplaceBeltrami(armadillo)

ks = [5, 15, 50, 200]

for k in ks:
    reconstructed_mesh = spectralAnalysis(armadillo, DLB, k)
    reconstructed_mesh.export('results/armadillo_{}.obj'.format(k))

#### Method that determies the resulted mesh after applying Diffusion Flow

In [11]:
def DiffusionFlow(mesh, l, max_iter):
    # Compute the discrete Laplace-Beltrami operator
    L = UniformLaplacian(mesh)
    res_mesh = mesh.copy()
    
    # Perform the diffusion flow
    for iter in range(max_iter):
        res_mesh.vertices = res_mesh.vertices + l * L @ res_mesh.vertices
    
    return res_mesh


#### Running the algorithm on multiple meshes with differnt number of iterations and lamdas

In [157]:

test_meshes = [cube, bunny, armadillo, camel]
test_names = ['cube', 'bunny', 'armadillo', 'camel']
test_iters = [5, 25, 50]
test_lambdas = [0.01, 0.1, 0.5]

# Perform the diffusion flow for each mesh and save the results
for mesh, name in zip(test_meshes, test_names):
    for l in test_lambdas:
        for iter in test_iters:
            res_mesh = DiffusionFlow(mesh, l, iter)
            res_mesh.export('results/q5/{}_{}_{}.obj'.format(name, l, iter))


#### Method that returns the mesh resulted after applying Implicit Smoothing

In [12]:
def ImplicitSmoothing(mesh, l):
    copy_mesh = mesh.copy()

    # Compute the discrete Laplace-Beltrami operator
    L = DiscreteLaplaceBeltrami(copy_mesh)

    # Determine A and b matrices to solve the linear system Ax = b
    A = np.eye(L.shape[0]) - l * L
    b = copy_mesh.vertices

    # Solve the linear system
    X = np.linalg.solve(A, b)

    # Update the vertices of the mesh
    copy_mesh.vertices = X
    
    return copy_mesh
    

#### Run the algorithm for different values of lambdas on different meshes and store the results

In [200]:
test_lambdas = [10 ** -6, 10 ** -3, 10 ** -2, 10 ** -1, 0.5]
test_meshes = [bunny, planens, fandiskns]
test_names = ['bunny', 'planens', 'fandiskns']

# Perform the implicit smoothing for each mesh and save the results
for mesh, name in zip(test_meshes, test_names):
    for l in test_lambdas:
        res_mesh = ImplicitSmoothing(mesh, l)
        res_mesh.export('results/q6/{}_{}.obj'.format(name, l))


#### Apply explicit and implicit smoothing on multiple meshes and with different levels of noise, having different values for lambdas

In [13]:
test_noise = [0.0001, 0.001, 0.01]
test_meshes = [bunny, planens, fandiskns]
test_names = ['bunny', 'planens', 'fandiskns']
test_lambdas = [10 ** -7, 10 ** -2, 0.1, 0.5, 1]

# Perform the implicit smoothing for each mesh and save the results
for mesh, name in zip(test_meshes, test_names):
    for l in test_lambdas:
        for noise in test_noise:
            noisy_mesh = mesh.copy()
            # Add noise to the vertices
            noisy_mesh.vertices += np.random.normal(0, noise, noisy_mesh.vertices.shape)
            
            # Perform the implicit smoothing
            res_mesh = ImplicitSmoothing(noisy_mesh, l)
            res_mesh.export('results/q7/Implicit/{}_{}_{}.obj'.format(name, l, noise))
            
            # Perform the diffusion flow
            res_mesh = DiffusionFlow(noisy_mesh, l, 1)
            res_mesh.export('results/q7/Diffusion/{}_{}_{}.obj'.format(name, l, noise))
